# New Business Emplacement Locator

The following project presents a way to provide recommendations to its user on which areas are more favorable to locate a new business, given the competition in the area and how atttractive it is to potential customers.

---------------

### INDEX

Please select the section of this workbook that you are interested on looking into:<br>

* [__Section 1:__ Data extraction and preparation](#cell1)<br>
* [__Section 2:__ Data analysis](#cell4)<br>
    <t> -> [KMeans analysis](#cell2)<br>
    <t> -> [DBSCAN analysis](#cell3)<br>

---------------------------------------------------------------------------------

<a id="cell1"></a>
# 1. Data extraction and preparation


The present section aims to scrape the postal codes and neighbourhoods of Toronto from the following link from <a href="https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M">Wikipedia</a>.


## 1.1. Importing libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis

!conda install -c conda-forge requests --yes 
import requests
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize
#FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead

import matplotlib.pyplot as plt # plotting library

!conda install -c conda-forge bs4 --yes 
from bs4 import BeautifulSoup

print("Libraries imported!")

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - requests


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    brotlipy-0.7.0             |py36h8c4c3a4_1000         346 KB  conda-forge
    chardet-3.0.4              |py36h9f0ad1d_1006         188 KB  conda-forge
    cryptography-2.9.2         |   py36h45558ae_0         613 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    pysocks-1.7.1              |   py36h9f0ad1d_1          27 KB  conda-forge
    urllib3-1.25.9             |             py_0          92 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.4 MB

The following NEW packages will be INSTALLED:

  brotlipy           conda-forge/linux-64::brotlipy-0.7.0-py3

## 1.2. Data Extraction

First step is to define the list of categories that are considered positive for the business as they attract people to them (sources) and those that are perceived as competitors, as their presence result into loss of potential customers (sinks).
The full list can be accessed here: https://developer.foursquare.com/docs/build-with-foursquare/categories/

In [53]:

#sources_list= ["College & University", "Arts & Entertainment", "Museum", "Music Venue", "Shopping Mall", "Shopping Plaza", "Train Station", "Stadium"]
#sources_ids=["4d4b7105d754a06372d81259", "4d4b7104d754a06370d81259", "4bf58dd8d48988d181941735","4bf58dd8d48988d1e5931735", "4bf58dd8d48988d1fd941735","5744ccdfe4b0c0459246b4dc","4bf58dd8d48988d129951735","4bf58dd8d48988d184941735"]


#Simplified list to reduce the number of Foursquare API calls
sources_list= [ "Arts & Entertainment","Music Venue", "Shopping Mall", "Stadium"]
sources_ids=[ "4d4b7104d754a06370d81259", "4bf58dd8d48988d1e5931735", "4bf58dd8d48988d1fd941735", "4bf58dd8d48988d184941735"]

sources_series = pd.Series(sources_ids, index=sources_list)

sinks_list=["Bar", "Tapas Restaurant", "Fast Food Restaurant", "Irish Pub"]
sinks_ids=["4bf58dd8d48988d116941735","4bf58dd8d48988d1db931735", "4bf58dd8d48988d16e941735", "52e81612bcbc57f1066b7a06"]

sinks_series = pd.Series(sinks_ids, index=sinks_list)

Second, the target city is defined, as well as the search parameters that will be used in the Foursquare calls

In [56]:
CLIENT_ID = 'LMLVNRBWW3CIYREB1ZHC01KN5TEEPSFCDJ0IKI1DWWC5DV4I' # your Foursquare ID
CLIENT_SECRET = 'JDMCB5IUYR2H4GTGOJ1FFUCATLSJVO0IXWGDBPGID4GSA1Q1' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
radius=1500
LIMIT=50

In [4]:
#Calculating Madrid coordinates to center the map in it
city = 'Madrid, ES'
geolocator = Nominatim(user_agent="city_explorer")
location = geolocator.geocode(city)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(city, latitude, longitude))

The geograpical coordinate of Madrid, ES are 40.4167047, -3.7035825.


As there will be various tasks that will be repeated, some functions will be created to simplify the code, as follows:
- __getlocations:__ This function will be taking care of making the calls to Foursquare and returning the venues in a dataframe format.
- __get_category_type:__ To extract the category type from a specific row in a dataframe
- __Get_filtered_df:__ This function cleans and makes a dataframe ready to be used.

In [5]:
def get_locations(list,lati,longi,search_radius):
    dataframe=pd.DataFrame()
    for value in list:
        search_query = value
        #url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, lati, longi, VERSION, search_query, radius, LIMIT)
        url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&categoryId={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, lati, longi, VERSION, search_query, search_radius, LIMIT)
        results = requests.get(url).json()
        # assign relevant part of JSON to venues
        venues = results['response']['venues']
        # tranform venues into a dataframe
        temp_dataframe = json_normalize(venues)
        temp_dataframe['PrimaryCategories'] = list[list==value].index[0]
        dataframe = [dataframe, temp_dataframe]
        dataframe = pd.concat(dataframe)
        # dropping ALL duplicte values 
        dataframe.drop_duplicates(subset ="id",keep = False, inplace = True) 
    if dataframe.empty==True:
        return pd.DataFrame([])
    else:
        return dataframe
 #dataframe.reset_index(inplace=True)    
#dataframe.head(10)

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']
    
def Get_filtered_df(dataframe):
    # keep only columns that include venue name, and anything that is associated with location
    filtered_columns = ['name', 'categories','PrimaryCategories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
    dataframe_filtered = dataframe.loc[:, filtered_columns]

    # filter the category for each row
    dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

    # clean column names by keeping only last term
    dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
    return dataframe_filtered

### 1.2.1. Neighbourhood information 

The data about the different neighbourhoods in our target city, Madrid, will be extracted from the wikipedia website (https://en.wikipedia.org/wiki/Districts_of_Madrid) via the BeautifulSoup library.

In [44]:
#---------------------
# Web data extraction
#---------------------
url="https://en.wikipedia.org/wiki/Districts_of_Madrid"
soup = BeautifulSoup(requests.get(url).content, "html.parser")

In [7]:
#----------------
# Reading table
#----------------
table=soup.find('table', class_="wikitable sortable")
#print(table.prettify())

#------------------------------------------------------------------------------
# Scanning through the table and extracting row info into a list (table_data)
#------------------------------------------------------------------------------
table_rows=table.find_all('tr')
table_data=[]
for tr in table_rows:
    td = tr.find_all('td')
    if len(td)>0:
        entry = [i.text for i in td]
        table_data.append(entry)
    
#------------------------------------------------
# Creating a df based on row info in table_tada
#------------------------------------------------
table_df=pd.DataFrame(table_data).iloc[:,:5]
table_df.rename(columns={0: "District number", 1: "Name", 2: "Size", 3: "Population", 4: "Pop density"}, inplace=True)
print(table_df.shape)
table_df.head(12)


(21, 5)


District number                   Name         Size Population Pop density
0              1\n               Centro\n     522.82\n  131,928\n    252.34\n
1              2\n           Arganzuela\n     646.22\n  151,965\n    235.16\n
2              3\n               Retiro\n     546.62\n  118,516\n    216.82\n
3              4\n            Salamanca\n     539.24\n  143,800\n    266.67\n
4              5\n            Chamartín\n     917.55\n  143,424\n    156.31\n
5              6\n               Tetuán\n     537.47\n  153,789\n    286.13\n
6              7\n             Chamberí\n     467.92\n  137,401\n    293.64\n
7              8\n  Fuencarral-El Pardo\n  23,783.84\n  238,756\n     10.04\n
8              9\n      Moncloa-Aravaca\n   4,653.11\n  116,903\n     25.12\n
9             10\n               Latina\n   2,542.72\n  233,808\n     91.95\n
10            11\n          Carabanchel\n   1,404.83\n  243,998\n    173.68\n
11            12\n                Usera\n     777.77\n  134,791\n    173.30\n

As it can be observed, the dataframe still needs some preparation and cleaning.

In [8]:
#----------------------------------
# DF cleaning and re-organisation
#----------------------------------
#Removing the \n 
table_df.replace(to_replace ='\n', value = '', regex = True, inplace=True)
table_df.head()

#Discarding not assigned boroughs (Not assigned / None)
table_df.drop(table_df.loc[ (table_df['Name'] == 'Not assigned')].index, inplace=True)
table_df.dropna(inplace=True)

#Removing the - 
table_df.replace(to_replace ='-', value = ',', regex = True, inplace=True)
table_df.head()

#Resetting the index
table_df.reset_index(inplace=True, drop=True)
table_df.head(10)

District number                 Name       Size Population Pop density
0               1               Centro     522.82    131,928      252.34
1               2           Arganzuela     646.22    151,965      235.16
2               3               Retiro     546.62    118,516      216.82
3               4            Salamanca     539.24    143,800      266.67
4               5            Chamartín     917.55    143,424      156.31
5               6               Tetuán     537.47    153,789      286.13
6               7             Chamberí     467.92    137,401      293.64
7               8  Fuencarral,El Pardo  23,783.84    238,756       10.04
8               9      Moncloa,Aravaca   4,653.11    116,903       25.12
9              10               Latina   2,542.72    233,808       91.95

Now the neighbourhood information is ready to be used!

### 1.2.2. Venues information

The next step is to do a scan for all the relevant venues. Since the maximun number of venues that can be fetched from Foursquare is limited to 50, several queries will need to be done in order to extract enough information. 

The approach to be followed will be for each neighbourhood, a request for each location category will be conducted. Since each neighbourhood has an arbitrary shape and the searches can only be performed in a circular basis format a big radius (1.5km) has been defined. Afterwards, the duplicated will be removed, in case some searches had elements overlapping. 

This type of scan may lead to blinds spots depending on the sizes of the neighbourhoods, which will have to be taken into consideration once the results are reviewed.


In [9]:
filtered_df=pd.DataFrame([])
neighbour_coords=pd.DataFrame([])

for value in table_df['Name']: # Loops that iterates for each neighbourhood
    city = value + ", Madrid, ES"
    geolocator = Nominatim(user_agent="city_explorer")
    location = geolocator.geocode(city)
    lati = location.latitude
    longi = location.longitude
    neighbour_coords  = pd.concat([neighbour_coords , pd.DataFrame([[value, lati, longi]])])
    print('The geograpical coordinate of {} are {}, {}.'.format(city, lati, longi))
#    temp_dataframe=get_locations(sources_series,lati,longi,radius)
#    if temp_dataframe.empty == False:
#        if filtered_df.empty==True:
#            filtered_df=Get_filtered_df(temp_dataframe)
#        else:
#            filtered_df= pd.concat([filtered_df, Get_filtered_df(temp_dataframe)])
neighbour_coords.rename(columns={0:'Name', 1:'lat',2:'lng'},inplace=True)    
filtered_df.head()

The geograpical coordinate of Centro, Madrid, ES are 40.417652700000005, -3.7079137662915533.
The geograpical coordinate of Arganzuela, Madrid, ES are 40.39806845, -3.6937339526567428.
The geograpical coordinate of Retiro, Madrid, ES are 40.4081555, -3.677441328098954.
The geograpical coordinate of Salamanca, Madrid, ES are 40.43152685, -3.6747257985730952.
The geograpical coordinate of Chamartín, Madrid, ES are 40.4607638, -3.677534058264615.
The geograpical coordinate of Tetuán, Madrid, ES are 40.46082135, -3.6995204270841526.
The geograpical coordinate of Chamberí, Madrid, ES are 40.43624735, -3.7038303534513837.
The geograpical coordinate of Fuencarral,El Pardo, Madrid, ES are 40.4947348, -3.6930692.
The geograpical coordinate of Moncloa,Aravaca, Madrid, ES are 40.4350196, -3.719236.
The geograpical coordinate of Latina, Madrid, ES are 40.4035317, -3.736152.
The geograpical coordinate of Carabanchel, Madrid, ES are 40.3742112, -3.744676.
The geograpical coordinate of Usera, Madrid,

Empty DataFrame
Columns: []
Index: []

In [10]:
print(table_df.shape,neighbour_coords.shape)

(21, 5) (21, 3)


In [55]:
neighbour_df = pd.merge(table_df, neighbour_coords, on='Name')
neighbour_df.head(10)

District number                 Name       Size Population Pop density  \
0               1               Centro     522.82    131,928      252.34   
1               2           Arganzuela     646.22    151,965      235.16   
2               3               Retiro     546.62    118,516      216.82   
3               4            Salamanca     539.24    143,800      266.67   
4               5            Chamartín     917.55    143,424      156.31   
5               6               Tetuán     537.47    153,789      286.13   
6               7             Chamberí     467.92    137,401      293.64   
7               8  Fuencarral,El Pardo  23,783.84    238,756       10.04   
8               9      Moncloa,Aravaca   4,653.11    116,903       25.12   
9              10               Latina   2,542.72    233,808       91.95   

         lat       lng  
0  40.417653 -3.707914  
1  40.398068 -3.693734  
2  40.408155 -3.677441  
3  40.431527 -3.674726  
4  40.460764 -3.677534  
5  40.460821 -3.699520  
6  40.436247 -3.703830  
7  40.494735 -3.693069  
8  40.435020 -3.719236  
9  40.403532 -3.736152

In [12]:
# dropping ALL duplicte values 
filtered_df.drop_duplicates(subset ="id",keep = False, inplace = True) 
#filtered_df.to_csv(r'Madrid Locations.csv', index = False)
filtered_df=pd.read_csv('Madrid Locations.csv') 

In [59]:
filtered_df.head()

name           categories     PrimaryCategories  \
0  Teatro Real de Madrid          Opera House  Arts & Entertainment   
1        Templo de Debod  Monument / Landmark  Arts & Entertainment   
2            Oh My Game!               Arcade  Arts & Entertainment   
3       Puerta de Alcalá  Monument / Landmark  Arts & Entertainment   
4         Puerta del Sol                Plaza  Arts & Entertainment   

                   address        lat       lng  distance postalCode  cc  \
0         Pl. de Isabel II  40.418226 -3.711064     274.0      28013  ES   
1             C. Ferraz, 1  40.423939 -3.717007    1040.0      28008  ES   
2                      NaN  40.431247 -3.699414    1675.0      28010  ES   
3  Pl. de la Independencia  40.420046 -3.688649    1654.0      28001  ES   
4       Pl. Puerta del Sol  40.417027 -3.703443     385.0      28013  ES   

  neighborhood    city   state country  \
0        Opera  Madrid  Madrid  España   
1          NaN  Madrid  Madrid  España   
2          NaN  Madrid  Madrid  España   
3          NaN  Madrid  Madrid  España   
4          NaN  Madrid  Madrid  España   

                                    formattedAddress  \
0  ['Pl. de Isabel II', '28013 Madrid Madrid', 'E...   
1  ['C. Ferraz, 1', '28008 Madrid Madrid', 'España']   
2                  ['28010 Madrid Madrid', 'España']   
3  ['Pl. de la Independencia', '28001 Madrid Madr...   
4  ['Pl. Puerta del Sol', '28013 Madrid Madrid', ...   

                                      labeledLatLngs crossStreet  \
0                                                NaN         NaN   
1                                                NaN         NaN   
2  [{'label': 'display', 'lat': 40.431247, 'lng':...         NaN   
3                                                NaN         NaN   
4                                                NaN         NaN   

                         id  
0  4adcda3cf964a5208c3d21e3  
1  4adcda37f964a520113c21e3  
2  5a8eff426bdee62e79a3dd0c  
3  4adcda37f964a5201b3c21e3  
4  4adcda37f964a5201f3c21e3

Now let's have a look at the summary of the information we will be using in the analysis:

In [13]:
dataframe_filtered=filtered_df
dataframe_filtered.groupby(['PrimaryCategories']).count()

name  categories  address  lat  lng  distance  \
PrimaryCategories                                                     
Arts & Entertainment   668         668      427  668  668       668   
Music Venue            292         292      215  292  292       292   
Shopping Mall          130         130       79  130  130       130   
Stadium                 38          38       19   38   38        38   

                      postalCode   cc  neighborhood  city  state  country  \
PrimaryCategories                                                           
Arts & Entertainment         313  668             9   502    502      668   
Music Venue                  169  292             0   245    245      292   
Shopping Mall                 63  130             3    96     96      130   
Stadium                       13   38             0    26     26       38   

                      formattedAddress  labeledLatLngs  crossStreet   id  
PrimaryCategories                                                         
Arts & Entertainment               668             658           47  668  
Music Venue                        292             292           32  292  
Shopping Mall                      130             130           19  130  
Stadium                             38              38            4   38

In [14]:
dataframe_filtered['PrimaryCategories'].unique()

array(['Arts & Entertainment', 'Music Venue', 'Shopping Mall', 'Stadium'],
      dtype=object)

## 1.3. Data visualization

Now it's time to visualize on the map the information we have available for the analysis, and see if the overall coverage is satisfactory as well.

In [58]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=10) # generate map centred around Madrid
from random import randint
colors = []

# Creating a random list of colors for each primary category
#The list of colors will be equal to the total number of categories, so we can differentiate them.
for i in range(dataframe_filtered['PrimaryCategories'].nunique()):
    colors.append('#%06X' % randint(0, 0xFFFFFF))
#A series is created so that the colors can be fetched later on, when drawing the markers
colors_df = pd.Series(colors, index=dataframe_filtered['PrimaryCategories'].unique())

# Now for each venue a circle marker will be placed
for lat, lng, label1, label2 in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.name, dataframe_filtered.PrimaryCategories):
    label= str(label1) + ", " + str(label2)
    folium.features.CircleMarker(
        [lat, lng],
        radius=4,
        color=colors_df[label2],
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color=colors_df[label2],
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map


<a id="cell4"></a>
## 2. Data Analysis

For analyzing the information and finding the best location for the business emplacement, the best approach is to identify clusters of venues that attract customers and therefore may have a positive impact in our business. <br>The algorithms that will be used to do so are K-means and DBSCAN. Both belong to the category of unsupervised learning.

<a id="cell2"></a>
### 2.1. K-Means analysis

This method has the positive side of returning results in a circular area, which is easy to analyse afterwards. It also allows the user to modify the number of clusters and get different proposals, which may produce different results.
On the downside, since all points need to be assigned to a cluster, outliers may increase dramatically the size of the clusters, providing the user a huge area as a recommendation.

#### 2.1.1. Cluster identification

KMeans library is imported and the number of clusters that we are requesting to be found is 24, since the area of Madrid is quite big.

In [60]:
from sklearn.cluster import KMeans 

In [64]:
k_means = KMeans(init="k-means++", n_clusters=24, n_init=16)

In [65]:
coords4cluster_df=dataframe_filtered[['lat', 'lng']]
coords4cluster_df.head()

lat       lng
0  40.418226 -3.711064
1  40.423939 -3.717007
2  40.431247 -3.699414
3  40.420046 -3.688649
4  40.417027 -3.703443

In [19]:
k_means.fit(coords4cluster_df)

KMeans(algorithm='auto', copy_x=True, init='k-means++', max_iter=300,
    n_clusters=24, n_init=16, n_jobs=None, precompute_distances='auto',
    random_state=None, tol=0.0001, verbose=0)

KMeans already has a build in function to provide the labels as well as the centers of the clusters, or _centroids_.

In [20]:
k_means_labels = k_means.labels_
k_means_cluster_centers = k_means.cluster_centers_
print(k_means_labels,k_means_cluster_centers)

[ 0 20  0 ... 16 16 16] [[40.42463106 -3.70461444]
 [40.4743177  -3.64506358]
 [40.45245888 -3.68997979]
 [40.40163037 -3.6668642 ]
 [40.38621462 -3.73662908]
 [40.44366461 -3.64606859]
 [40.49034542 -3.7039243 ]
 [40.40790141 -3.69641686]
 [40.41146364 -3.63319543]
 [40.34508069 -3.69788624]
 [40.42446245 -3.6706353 ]
 [40.49858539 -3.68719887]
 [40.38720705 -3.70057229]
 [40.40865135 -3.74535391]
 [40.38718013 -3.65439309]
 [40.44677801 -3.67034137]
 [40.47283491 -3.57637447]
 [40.46604016 -3.6900095 ]
 [40.42874887 -3.61060999]
 [40.44735642 -3.70379298]
 [40.43345052 -3.71753758]
 [40.42469643 -3.6868102 ]
 [40.37387817 -3.74909064]
 [40.41180324 -3.7206578 ]]


In [66]:
clustered_df= dataframe_filtered[['PrimaryCategories','name','lat','lng']]
clustered_df['Labels'] = k_means_labels
clustered_df.head(10)

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


PrimaryCategories                        name        lat       lng  \
0  Arts & Entertainment       Teatro Real de Madrid  40.418226 -3.711064   
1  Arts & Entertainment             Templo de Debod  40.423939 -3.717007   
2  Arts & Entertainment                 Oh My Game!  40.431247 -3.699414   
3  Arts & Entertainment            Puerta de Alcalá  40.420046 -3.688649   
4  Arts & Entertainment              Puerta del Sol  40.417027 -3.703443   
5  Arts & Entertainment                 Kilómetro 0  40.416831 -3.703840   
6  Arts & Entertainment                 Museo metro  40.431658 -3.700583   
7  Arts & Entertainment            Plaza de Cibeles  40.419191 -3.693117   
8  Arts & Entertainment   Guernica By Pablo Picasso  40.408134 -3.694328   
9  Arts & Entertainment  Iglesia Del Corpus Christi  40.415006 -3.709484   

   Labels  
0       0  
1      20  
2       0  
3      21  
4       0  
5       0  
6       0  
7      21  
8       7  
9       0

As the labels havbe been added to the dataframe with the venues, _clustered_df_ we can continue processing the information from KMeans. For example obtaining the centroid coordinates.

In [67]:
centroids_df= pd.DataFrame(k_means_cluster_centers)
centroids_df.rename(columns={0: 'lat', 1: 'lng'}, inplace=True)
centroids_df

lat       lng
0   40.424631 -3.704614
1   40.474318 -3.645064
2   40.452459 -3.689980
3   40.401630 -3.666864
4   40.386215 -3.736629
5   40.443665 -3.646069
6   40.490345 -3.703924
7   40.407901 -3.696417
8   40.411464 -3.633195
9   40.345081 -3.697886
10  40.424462 -3.670635
11  40.498585 -3.687199
12  40.387207 -3.700572
13  40.408651 -3.745354
14  40.387180 -3.654393
15  40.446778 -3.670341
16  40.472835 -3.576374
17  40.466040 -3.690009
18  40.428749 -3.610610
19  40.447356 -3.703793
20  40.433451 -3.717538
21  40.424696 -3.686810
22  40.373878 -3.749091
23  40.411803 -3.720658

Let's visualize the result for a better understanding of where the clusters are located.

In [23]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=11) # generate map centred in Madrid

from random import randint
colors = []
#-------------------------------------------------------------------------------CHange colors generator method!
#colors = plt.cm.Spectral(np.linspace(0, 1, len(set(k_means_labels))))

# Creating a random list of colors for each primary category
#First, a list of colors, equal to the total number of categories is created
for i in range(clustered_df['Labels'].nunique()):
    colors.append('#%06X' % randint(0, 0xFFFFFF))
#A series is created so that the colors can be fetched later on, when drawing the markers
colors_df = pd.Series(colors, index=clustered_df['Labels'].unique())
    
# Adding the locations as circle markers
for lat, lng, label1, label2 in zip(clustered_df.lat, clustered_df.lng, clustered_df.Labels, clustered_df.PrimaryCategories):
    label= "Cluster#" + str(label1) + ", " + str(label2)
    folium.features.CircleMarker(
        [lat, lng],
        radius=3,
        color=colors_df[label1],
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color=colors_df[label1],
        fill_opacity=0.6
    ).add_to(venues_map)
    
# Adding the cluster centroids
for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
    label= "Cluster#" + str(index)
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='red',
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color='red',
        fill_opacity=0.8
    ).add_to(venues_map)
    

# Displaying map
venues_map

As a validation step, let's see how the centroids compare to the center of the neighbourhoods.

In [24]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=11) # generate map centred in Madrid
   
# Adding the cluster centroids
for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
    label= "Cluster#" + str(index)
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='red',
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color='red',
        fill_opacity=0.8
    ).add_to(venues_map)
    

# Adding the neighbourhood centers
for lat, lng, label, in zip(neighbour_df.lat, neighbour_df.lng, neighbour_df.Name):
    label= "Neighbourhood " + label
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color='blue',
        fill_opacity=0.8
    ).add_to(venues_map)

# Displaying map
venues_map

Is it can be seen, in the outskirts of the city, where some neighbourhoods are isolated, we can see how the cluster centroids are really close to the center of the neighbourhoods, while in the core of the city they are differently distributed.

#### 2.1.2. Cluster values

In order to provide a recommendation of which clusters are more favorable, the following method will be applied:<br>
- Calculating the average radius of each neighbouthood, to limit the impact of the outliers.
- Scan each cluster for the source and sink venues. 
- Calculate the difference between source and sink venues.
- Positive values indicate a bigger presence of venues that attract customers with less competitors around them.

The function calculates the distance between two coodinates. It turned out to be more ellaborated than initially expected (euclidean distance), given the curvature of the Earth. The result is as follows:


In [25]:
# This function calculates the distance between two coodinates
from math import sin, cos, sqrt, atan2, radians
def distance_calculator(lat1,lng1,lat2,lng2):
    # approximate radius of earth in km
    R = 6373.0
    lat1 = radians(lat1)
    lng1 = radians(lng1)
    lat2 = radians(lat2)
    lng2 = radians(lng2)
    
    dlng = lng2 - lng1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlng / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c
    return distance

In [26]:
clusters_radius= dict()

for clusternum in range(clustered_df['Labels'].nunique()):
    temp_cluster_radius=dict()
    for index, row in clustered_df[clustered_df.Labels.eq(clusternum)].iterrows():
        temp_cluster_radius[index]=distance_calculator(centroids_df.loc[clusternum].lat,centroids_df.loc[clusternum].lng,row.lat,row.lng)
    #clusters_radius[clusternum]=max(pd.Series(temp_cluster_radius).values)*1000
    clusters_radius[clusternum]=sum(pd.Series(temp_cluster_radius).values)/len(pd.Series(temp_cluster_radius).values)*1000

C_radius=np.array(pd.DataFrame(clusters_radius.items()).drop(columns=0))

print(C_radius)

[[ 568.19716382]
 [ 999.93238567]
 [ 517.0466618 ]
 [ 850.12557715]
 [ 641.34727766]
 [1077.81507326]
 [ 819.13413848]
 [ 587.7007586 ]
 [ 915.65314477]
 [1153.63610516]
 [ 634.08755804]
 [ 889.74477051]
 [ 743.84526221]
 [ 723.64963535]
 [ 821.38204421]
 [ 743.48542172]
 [1035.88474251]
 [ 600.94625904]
 [ 937.35992864]
 [ 737.41630175]
 [ 675.39928372]
 [ 577.14885978]
 [ 924.95745562]
 [ 840.28373316]]


Now that we have the radius of the areas that we will scan around the cluster centroids, let's see how they look on the map. It's worth noting that with this method some information will be lost, so as a precaution it could be worth using the maximun distance from the centroid to the points of that cluster by uncommenting the calculation row in the previous step.

In [27]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=11) # generate map centred around Madrid

# Adding the cluster centroids
for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
    label= "Cluster#" + str(index)
    folium.features.Circle(
        [lat, lng],
        radius=int(C_radius[index]),
        color='blue'
    ).add_to(venues_map)
    
# display map
venues_map

Now it's time to calculate the value of each cluster!

In [28]:
sources_dataframe=pd.DataFrame([])
sinks_dataframe=pd.DataFrame([])
filtered_sources_df=pd.DataFrame([])
filtered_sinks_df=pd.DataFrame([])
cluster_val=dict()

#for each cluster, source and sink venues are fetched from Foursquare according to the lists defined in the begining of the notebook

for index,row in centroids_df.iterrows():
    city ="Cluster #" + str(index)
    geolocator = Nominatim(user_agent="city_explorer")
    location = geolocator.geocode(city)
    lati = row.lat
    longi = row.lng
    print('The geograpical coordinates of {} are {}, {}.'.format(city, lati, longi))
    
    sources_dataframe=get_locations(sources_series,lat,longi,clusters_radius[index])
    if sources_dataframe.empty == False:
        filtered_sources_df=Get_filtered_df(sources_dataframe)
    
    sinks_dataframe=get_locations(sinks_series,lati,longi,clusters_radius[index])
    if sinks_dataframe.empty == False:
        filtered_sinks_df=Get_filtered_df(sinks_dataframe)
        
    #Calculating cluster value based on the difference in the number of locations
    cluster_val[index]=filtered_sources_df.shape[0]-filtered_sinks_df.shape[0]
    
cluster_val

The geograpical coordinates of Cluster #0 are 40.42463105959468, -3.704614436412321.


/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:11: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  # This is added back by InteractiveShellApp.init_path()


The geograpical coordinates of Cluster #1 are 40.474317697311726, -3.6450635814440324.
The geograpical coordinates of Cluster #2 are 40.45245888439669, -3.6899797850868166.
The geograpical coordinates of Cluster #3 are 40.40163036575853, -3.666864196250821.
The geograpical coordinates of Cluster #4 are 40.38621462216296, -3.736629075486272.
The geograpical coordinates of Cluster #5 are 40.44366460572619, -3.6460685917395206.
The geograpical coordinates of Cluster #6 are 40.49034542083974, -3.7039242986908567.
The geograpical coordinates of Cluster #7 are 40.407901406640974, -3.696416864853866.
The geograpical coordinates of Cluster #8 are 40.411463639600385, -3.633195433119533.
The geograpical coordinates of Cluster #9 are 40.34508068515972, -3.697886240389643.
The geograpical coordinates of Cluster #10 are 40.42446245038628, -3.670635301671646.
The geograpical coordinates of Cluster #11 are 40.49858539374987, -3.687198871304032.
The geograpical coordinates of Cluster #12 are 40.387207

{0: -59,
 1: -27,
 2: -39,
 3: -37,
 4: -1,
 5: -67,
 6: 64,
 7: -49,
 8: -10,
 9: 73,
 10: -91,
 11: 35,
 12: 42,
 13: 32,
 14: -18,
 15: -53,
 16: -29,
 17: -12,
 18: -17,
 19: -24,
 20: -62,
 21: -51,
 22: 21,
 23: -33}

In [29]:
#filtered_sources_df.to_csv(r'Sources Locations.csv', index = False)
#filtered_sinks_df.to_csv(r'Sinks Locations.csv', index = False)

In [78]:
# Displaying the cluster values
for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
    if cluster_val[index]>0:
        print("\033[1;32m Cluster#" + str(index) + ' total value: ' + str(cluster_val[index]))
    else:   
        print("\033[1;31m Cluster#" + str(index) + ' total value: ' + str(cluster_val[index]))
    

 Cluster#0 total value: -59
 Cluster#1 total value: -27
 Cluster#2 total value: -39
 Cluster#3 total value: -37
 Cluster#4 total value: -1
 Cluster#5 total value: -67
 Cluster#6 total value: 64
 Cluster#7 total value: -49
 Cluster#8 total value: -10
 Cluster#9 total value: 73
 Cluster#10 total value: -91
 Cluster#11 total value: 35
 Cluster#12 total value: 42
 Cluster#13 total value: 32
 Cluster#14 total value: -18
 Cluster#15 total value: -53
 Cluster#16 total value: -29
 Cluster#17 total value: -12
 Cluster#18 total value: -17
 Cluster#19 total value: -24
 Cluster#20 total value: -62
 Cluster#21 total value: -51
 Cluster#22 total value: 21
 Cluster#23 total value: -33


The way the recommendations will be provided will be over the map, in green those clusters with positive values and in red those with negative.

In [87]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=11) # generate map centred around Madrid
    
# Adding the cluster centroids
for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
    label= "Cluster#" + str(index) + 'Total Value: ' + str(cluster_val[index])
    if cluster_val[index]>0:
        cluster_value_color='green'
    else:
        cluster_value_color='red'
    folium.features.CircleMarker(
        [lat, lng],
        radius=2,
        color=cluster_value_color,
        popup=folium.Popup(label, parse_html=True, max_width='100%'),
        fill = True,
        fill_color=cluster_value_color,
        fill_opacity=0.8
    ).add_to(venues_map)
    
    # Adding the cluster areas
    folium.features.Circle(
        [lat, lng],
        radius=int(C_radius[index]),
        color=cluster_value_color
    ).add_to(venues_map)
    
    
# display map
venues_map

<a id="cell3"></a>
### 2.2. DBSCAN

This method has the advantage of finding clusters of irregular shape, making it more precise. The user has the flexibility in this case to define how restrictive the model is by defining epsilon and the minimum number of samples of each cluster. <br> On the downside, given the fact that information from foursquare can only be fetched in circles, this complicates the value calculation of each cluster. 


#### 2.2.1. Cluster identification

In [89]:
import numpy as np 
from sklearn.cluster import DBSCAN 
from sklearn.datasets.samples_generator import make_blobs 
from sklearn.preprocessing import StandardScaler 
import matplotlib.pyplot as plt 
%matplotlib inline

In [32]:
epsilon = 0.15
minimumSamples = 10
DBSCAN_coords4cluster_df_std= StandardScaler().fit_transform(coords4cluster_df)
db = DBSCAN(eps=epsilon, min_samples=minimumSamples).fit(DBSCAN_coords4cluster_df_std)
DBSCAN_labels = db.labels_
DBSCAN_labels

array([ 0,  0,  0, ..., -1, -1, -1])

In [33]:
DBSCAN_clustered_df= dataframe_filtered[['PrimaryCategories','name','lat','lng']]
#DBSCAN_clustered_df.drop(columns= 'Labels', inplace=True)
#DBSCAN_clustered_df['Labels'] = pd.Series(DBSCAN_labels).to_frame()
DBSCAN_clustered_df['Labels'] = DBSCAN_labels
DBSCAN_clustered_df


/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


PrimaryCategories                              name        lat  \
0     Arts & Entertainment             Teatro Real de Madrid  40.418226   
1     Arts & Entertainment                   Templo de Debod  40.423939   
2     Arts & Entertainment                       Oh My Game!  40.431247   
3     Arts & Entertainment                  Puerta de Alcalá  40.420046   
4     Arts & Entertainment                    Puerta del Sol  40.417027   
...                    ...                               ...        ...   
1123  Arts & Entertainment       centro cultural paracuellos  40.469091   
1124  Arts & Entertainment           El Boulevar T2, Loteria  40.468105   
1125  Arts & Entertainment                   Oficina turismo  40.490292   
1126  Arts & Entertainment  Administración de Loterías N°165  40.468411   
1127  Arts & Entertainment               Galeria De Fotos T1  40.468275   

           lng  Labels  
0    -3.711064       0  
1    -3.717007       0  
2    -3.699414       0  
3    -3.688649       0  
4    -3.703443       0  
...        ...     ...  
1123 -3.580031      -1  
1124 -3.568698      -1  
1125 -3.592681      -1  
1126 -3.569884      -1  
1127 -3.570579      -1  

[1128 rows x 5 columns]

In [91]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=12) # generate map centred around the Conrad Hotel

from random import randint
colors = []

# Creating a random list of colors for each primary category
#First, a list of colors, equal to the total number of categories is created
for i in range(DBSCAN_clustered_df['Labels'].nunique()):
    colors.append('#%06X' % randint(0, 0xFFFFFF))
#A series is created so that the colors can be fetched later on, when drawing the markers
colors_df = pd.Series(colors, index=DBSCAN_clustered_df['Labels'].unique())

# add the locations as circle markers
for lat, lng, label1, label2 in zip(DBSCAN_clustered_df.lat, DBSCAN_clustered_df.lng, DBSCAN_clustered_df.Labels, DBSCAN_clustered_df.PrimaryCategories):
    if label1 > -1:
        label= "Cluster#" + str(label1) + ", " + str(label2)
        folium.features.CircleMarker(
            [lat, lng],
            radius=5,
            color=colors_df[label1],
            popup=folium.Popup(label, parse_html=True, max_width='100%'),
            fill = True,
            fill_color=colors_df[label1],
            fill_opacity=0.6
        ).add_to(venues_map)

# display map
venues_map

To facilitate the task of scanning the clusters, the approach to be followed will be to approximate them to circles by calculating first the centroid location and the average radius.

In [35]:
#DBSCAN_Centroids=pd.DataFrame(np.unique(DBSCAN_clustered_df['Labels'].values), columns=['Labels'])
DBSCAN_Centroids=DBSCAN_clustered_df[['Labels','lat','lng']].groupby(['Labels']).sum()/DBSCAN_clustered_df[['Labels','lat','lng']].groupby(['Labels']).count()
DBSCAN_Centroids.reset_index(inplace=True)
DBSCAN_Centroids

Labels        lat       lng
0      -1  40.425447 -3.679887
1       0  40.421392 -3.699825
2       1  40.389146 -3.699757
3       2  40.427243 -3.667006
4       3  40.443247 -3.670290
5       4  40.456154 -3.692189
6       5  40.385711 -3.739756
7       6  40.414575 -3.726885
8       7  40.392846 -3.659758
9       8  40.472595 -3.636143

In [36]:
DBSCAN_clusters_radius= dict()
for clusternum in range(DBSCAN_Centroids['Labels'].nunique()):
    temp_cluster_radius=dict()
    for index, row in DBSCAN_clustered_df[DBSCAN_clustered_df.Labels.eq(clusternum-1)].iterrows():
        temp_cluster_radius[index]=distance_calculator(DBSCAN_Centroids.loc[clusternum].lat,DBSCAN_Centroids.loc[clusternum].lng,row.lat,row.lng)
    DBSCAN_clusters_radius[clusternum-1]=sum(pd.Series(temp_cluster_radius).values)/len(pd.Series(temp_cluster_radius).values)*1000
    #DBSCAN_clusters_radius[clusternum-1]=max(pd.Series(temp_cluster_radius).values)*1000
    
DBSCAN_C_radius=np.array(pd.DataFrame(DBSCAN_clusters_radius.items()).drop(columns=0))

print(DBSCAN_C_radius)

[[5373.45224563]
 [1256.24237426]
 [ 458.88891094]
 [ 398.16863492]
 [ 595.13866129]
 [ 854.29279659]
 [ 311.29083477]
 [ 241.21526094]
 [ 261.75804435]
 [ 238.05787923]]


In [90]:
DBSCAN_Centroids['radius']=DBSCAN_C_radius
DBSCAN_Centroids

Labels        lat       lng       radius
0      -1  40.425447 -3.679887  5373.452246
1       0  40.421392 -3.699825  1256.242374
2       1  40.389146 -3.699757   458.888911
3       2  40.427243 -3.667006   398.168635
4       3  40.443247 -3.670290   595.138661
5       4  40.456154 -3.692189   854.292797
6       5  40.385711 -3.739756   311.290835
7       6  40.414575 -3.726885   241.215261
8       7  40.392846 -3.659758   261.758044
9       8  40.472595 -3.636143   238.057879

Let's see how the areas that will be analyze look like on the map:

In [38]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=12) # generate map centred around Madrid

# Adding the cluster centroids
for lat, lng, index,c_radius in zip(DBSCAN_Centroids.lat, DBSCAN_Centroids.lng, DBSCAN_Centroids.Labels,DBSCAN_Centroids.radius):
    if index>=0:
        label= "Cluster#" + str(index)
        folium.features.Circle(
            [lat, lng],
            radius=c_radius,
            color='blue'
        ).add_to(venues_map)
    
# display map
venues_map

#### 2.2.2. Cluster values

The method to calculate the cluster values will be the same as for KMeans, despite this may lead to some deviations from the original cluster shape provided by DBSCAN. An alternative way would be to scan each venue in each cluster for competitors around them and removing the duplicates, but given the limitation of API calls that can be done to Foursquare, this method has been discarded.

In [39]:
sources_dataframe=pd.DataFrame([])
sinks_dataframe=pd.DataFrame([])
filtered_sources_df=pd.DataFrame([])
filtered_sinks_df=pd.DataFrame([])
DBSCAN_cluster_val=dict()

#for index,row in DBSCAN_Centroids.iterrows():
for lat, lng, index,c_radius in zip(DBSCAN_Centroids.lat, DBSCAN_Centroids.lng, DBSCAN_Centroids.Labels,DBSCAN_Centroids.radius):
    if index>=0:
        city ="Cluster #" + str(index)
        geolocator = Nominatim(user_agent="city_explorer")
        location = geolocator.geocode(city)
        lati = row.lat
        longi = row.lng
        print('The geograpical coordinates of {} are {}, {}.'.format(city, lati, longi))

        sources_dataframe=get_locations(sources_series,lat,longi,c_radius)
        if sources_dataframe.empty == False:
            filtered_sources_df=Get_filtered_df(sources_dataframe)

        sinks_dataframe=get_locations(sinks_series,lati,longi,c_radius)
        if sinks_dataframe.empty == False:
            filtered_sinks_df=Get_filtered_df(sinks_dataframe)

        #Calculating cluster value based on the difference in the number of locations
        DBSCAN_cluster_val[index]=filtered_sources_df.shape[0]-filtered_sinks_df.shape[0]
    else:
        DBSCAN_cluster_val[index]=0
        
DBSCAN_cluster_val

The geograpical coordinates of Cluster #0 are 40.4722389940381, -3.6356243433096154.


/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:11: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  # This is added back by InteractiveShellApp.init_path()


The geograpical coordinates of Cluster #1 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #2 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #3 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #4 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #5 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #6 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #7 are 40.4722389940381, -3.6356243433096154.
The geograpical coordinates of Cluster #8 are 40.4722389940381, -3.6356243433096154.


{-1: 0, 0: -37, 1: -14, 2: -5, 3: -12, 4: -22, 5: 10, 6: 11, 7: 11, 8: -2}

In [93]:
# Displaying the cluster values
for lat, lng, index,c_radius in zip(DBSCAN_Centroids.lat, DBSCAN_Centroids.lng, DBSCAN_Centroids.Labels,DBSCAN_Centroids.radius):
    if DBSCAN_cluster_val[index]>0:
        print("\033[1;32m Cluster#" + str(index) + ' total value: ' + str(DBSCAN_cluster_val[index]))
    else:   
        print("\033[1;31m Cluster#" + str(index) + ' total value: ' + str(DBSCAN_cluster_val[index]))
    

 Cluster#-1 total value: 0
 Cluster#0 total value: -37
 Cluster#1 total value: -14
 Cluster#2 total value: -5
 Cluster#3 total value: -12
 Cluster#4 total value: -22
 Cluster#5 total value: 10
 Cluster#6 total value: 11
 Cluster#7 total value: 11
 Cluster#8 total value: -2


The final recommendation looks as follows:

In [51]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=11) # generate map centred in Madrid
    
# Adding the cluster centroids
#for lat, lng, index in zip(centroids_df.lat, centroids_df.lng, set(k_means_labels)):
for lat, lng, index,c_radius in zip(DBSCAN_Centroids.lat, DBSCAN_Centroids.lng, DBSCAN_Centroids.Labels,DBSCAN_Centroids.radius):
    if index>=0:
        label= "Cluster#" + str(index) + 'Total Value: ' + str(DBSCAN_cluster_val[index])
        if DBSCAN_cluster_val[index]>0:
            DBSCAN_cluster_value_color='green'
        else:
            DBSCAN_cluster_value_color='red'
        folium.features.CircleMarker(
            [lat, lng],
            radius=2,
            color=DBSCAN_cluster_value_color,
            popup=folium.Popup(label, parse_html=True, max_width='100%'),
            fill = True,
            fill_color=DBSCAN_cluster_value_color,
            fill_opacity=0.8
        ).add_to(venues_map)

        # Adding the cluster areas
        folium.features.Circle(
            [lat, lng],
            radius=int(c_radius ),
            color=DBSCAN_cluster_value_color
        ).add_to(venues_map)

    
# Adding the neighbourhood densities
#for lat, lng, label, density in zip(neighbour_df.lat, neighbour_df.lng, neighbour_df.Name, neighbour_df['Pop density']):
#    label= "Neighbourhood " + label +", density:"+ str(density)
#    folium.features.CircleMarker(
#        [lat, lng],
#        radius=6,
#        color='blue',
#        popup=folium.Popup(label, parse_html=True, max_width='100%'),
#        fill = True,
#        fill_color='blue',
#        fill_opacity=0.8
#    ).add_to(venues_map)
        
# display map
venues_map

Thanks for reading!